In [ ]:
import numpy as np
import pandas as pd
import keras as keras

In [ ]:
from keras.datasets import mnist
(train_X, train_y), (test_X, test_y) = mnist.load_data()

11490434/11490434 [==============================] - 0s 0us/step


In [ ]:
train_X.shape

(60000, 28, 28)

In [ ]:
type(train_X)

numpy.ndarray

In [ ]:
train_y

array([5, 0, 4, ..., 5, 6, 8], dtype=uint8)

In [ ]:
28*28


784

In [ ]:
train = []
for i in range(len(train_X)):
  train.append(np.reshape(train_X[i], (1, 784)))

x_train = np.array(train)
y_train = train_y

In [ ]:
y_train = np.reshape(train_y, (len(train_y)))

In [ ]:
# Preprocessing
for i in range(len(x_train)):
  for j in range(len(x_train[i][0])):
    if x_train[i][0][j] > 0 :
      x_train[i][0][j] = 1

In [ ]:
x_train[0].shape

(1, 784)

In [ ]:
x_train[0]

array([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1,
        1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 

In [ ]:
# Input neurons = 784
# Output neurons = 10

In [ ]:
y_train[0]

5

In [ ]:
# Process y
new_y_train = []
for i in range(len(y_train)):
  l = np.zeros((10))
  l[y_train[i]]=1
  new_y_train.append(l)

y_train = np.array(new_y_train)


In [ ]:
x_train.shape

(60000, 1, 784)

In [ ]:
y_train.shape

(60000, 10)

In [ ]:
temp = np.zeros((60000,1,10))
for i in range(60000):
  for j in range(10):
    temp[i][0][j] = y_train[i][j]
y_train = temp

In [ ]:
y_train.shape

(60000, 1, 10)

Now we will make a helper class for the difference activation functions

In [ ]:
class Activation:
  # x is (1,size)
  def sigmoid(self,x):
    for i in range(x.shape[1]):
      x[0][i] = 1/(1+np.exp(-x[0][i]))
    return x
  # def tanh(x):
  #   return np.tanh(x)
  # def relu(x):
  #   return np.maximum(x,0)
  def sigmoid_der(self, x):
    for i in range(x.shape[1]):
      x[0][i] = x[0][i]*(1-x[0][i])

    return x*(1-x)
  # def tanh_der(x):
  #   return 1-np.power(np.tanh(x), 2)
  # def relu_der(x):
  #   return np.where(x >= 0, 1, 0)

Helper metrics class

In [ ]:
class Metrics:
  def __init__(self, y_pred, y_test):
    self.y_pred = y_pred
    self.y_actual = y_test
    self.len = len(y_pred)

  def equal(self):
    # Count the number of matching elements
    max_index = -1
    max = 0
    y_modified = np.zeros_like(self.y_actual)
    for i in range(self.y_pred.shape[1]):
      if max<self.y_pred[0][i]:
        max = self.y_pred[0][i]
        max_index = i
    for i in range(self.y_pred.shape[1]):
      if i!=max_index:
        y_modified[0][i] = 0
      else:
        y_modified[0][i] = 1
    return np.array_equal(y_modified, self.y_actual)



  def mean_square_error(self):
    return np.mean(np.power(self.y_pred - self.y_actual, 2))



# Making the layers for the library

It's properties are:
 1. It takes an input from a previous layer
 2. It gives and output to the next layer
 3. It computes the output through forward propogation
 4. It updates it's parameters through back propogation

In [ ]:
# class Layer:
#   def __init__(self):
#     self.input = None
#     self.output = None

#   def foward_propogate(self, input):
#     raise NotImplemenetedError

#   def backward_propogate(self, output_error, lr):
#     raise NotImplementedError

Let us define a Dense Layer (where every neuron is connected to every other neuron in the next layer) which is a subclass of our Layer class.

In [ ]:
class DenseLayer():
  # input_size = no of neurons in layer
  # output_size = no of neurons in next layer
  def __init__(self, input_size, output_size, activation):
    # weights is an array of input_size rows and output_size columns
    # i-th row j-th column is the weight connecting i-th output neuron to j-th input neuron
    self.weights = np.zeros((input_size, output_size))
    # Apart from these there must be a bias neuron that is connected to all the output neurons
    self.bias = np.zeros((1,output_size))
    # Activation Function for this layer
    self.activation = activation
    # Input values, activation (weighted avg of input), outputs (activation function applied on activations), errors (of each neuron)
    self.inputs = np.zeros((1, input_size))
    self.activations = np.zeros((1, output_size))
    self.outputs = np.zeros((1, output_size))
    self.input_errors = np.zeros((1, input_size))

  # Given the input calculate the outputs (using the weights)
  # Input is a numpy array of 1 rows and input_size columns
  # Output is a numpy array of 1 rows and output_size columns
  def forward_propogate(self, inputs):
    self.inputs = inputs
    self.activations = np.dot(self.inputs, self.weights) + self.bias
    ac = Activation()
    match self.activation:
      case "relu":
        self.output = ac.relu(self.activations)
      case "sigmoid":
        # print(self.activations.shape)
        self.output = ac.sigmoid(self.activations)
      case "tanh":
        self.output = ac.tanh(self.activations)
    return self.output

  # output_errors is a numpy array with 1 rows and output_size columns
  # Because it coressponds to errors at output_size neurons
  def backward_propogate(self, output_errors, lr):
    ac = Activation()
    # (IS,OS)x(output_size,1).T = (1,input_size)
    # backpropogate the errors
    match self.activation:
      case "relu":
        self.input_errors = ac.relu_der(self.inputs)*(np.dot(self.weights, output_errors.T)).T
      case "sigmoid":
        # (1,IS)*[(1S,OS)x(OS,1)].T
        self.input_errors = ac.sigmoid_der(self.inputs)*(np.dot(self.weights, output_errors.T)).T
      case "tanh":
        self.input_errors = ac.tanh_der(self.inputs)*(np.dot(self.weights, output_errors.T)).T
    # Calculate the error in weights for this layer
    weight_errors = np.dot(self.inputs.T, output_errors)
    # Update the weights
    self.weights -= lr*weight_errors
    # Update the bias
    self.bias -= lr*output_errors


# Neural Network Class

Will have all our dense layers (and the initial layer and final layer)

In [ ]:
class NeuralNetwork:
  def __init__(self):
    self.layers = []
    self.loss = None

  # Add a layer to our model
  def add(self, layer):
    self.layers.append(layer)
    return

  # Predict Output (through forward propogation)
  def predict(self, input_data):
    y_pred = []
    # Run the neural network over all the samples
    for i in range(len(input_data)):
      # Forward propogate the values
      output = input_data[i]
      for layer in self.layers:
        output = layer.forward_propogate(output)
      # output_shape = (1,final_output_size (output_size of last layer))
      y_pred.append(output)
    return y_pred

  # Train the network
  # x_train = (60,000,1,780)
  # y_train = (60,000, 1, 10)
  def fit(self, x_train, y_train, epochs=10, lr=0.001):
    self.loss = []
    misclassifications = 0
    for i in range(epochs):
      misclassifications = 0
      print("epochs: "+str(i))
      print("loss:" + str(self.loss))
      for j in range(len(x_train)):
        errors = 0
        # Forward propogate the values
        output = x_train[i]
        for layer in self.layers:
          output = layer.forward_propogate(output)
        # now we have the predicted outputs
        # Calculate the error at the end
        errors = output - y_train[i]
        # Store the loss
        metrics = Metrics(output, y_train[i])
        self.loss.append((i,metrics.mean_square_error()))
        if not metrics.equal(): misclassifications = misclassifications+1
        if j%1000 == 0:
          print(j)
          print(self.loss)
          print(output)
        # Backpropogate the errors
        for layer in reversed(self.layers):
          errors = layer.backward_propogate(errors, lr)
    print("misclassifications:"+str(misclassifications))

In [ ]:
nn = NeuralNetwork()
dl = DenseLayer(784, 10, "sigmoid")
nn.add(dl)
nn.fit(x_train, y_train)

epochs: 0
loss:[]
0
[(0, 0.25)]
[[0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5]]
1000
[(0, 0.25), (0, 0.2498750156276035), (0, 0.24975009375519042), (0, 0.24962523436709097), (0, 0.24950043744760775), (0, 0.24937570298101663), (0, 0.24925103095156625), (0, 0.24912642134347815), (0, 0.24900187414094668), (0, 0.24887738932813944), (0, 0.24875296688919696), (0, 0.24862860680823343), (0, 0.24850430906933557), (0, 0.24838007365656387), (0, 0.24825590055395214), (0, 0.24813178974550726), (0, 0.24800774121521024), (0, 0.2478837549470146), (0, 0.24775983092484846), (0, 0.24763596913261304), (0, 0.24751216955418337), (0, 0.2473884321734082), (0, 0.24726475697411027), (0, 0.24714114394008585), (0, 0.2470175930551058), (0, 0.2468941043029141), (0, 0.24677067766722954), (0, 0.24664731313174465), (0, 0.24652401068012592), (0, 0.2464007702960148), (0, 0.24627759196302618), (0, 0.24615447566474996), (0, 0.24603142138475004), (0, 0.24590842910656502), (0, 0.24578549881370776), (0, 0.245662630489666), (0, 0

In [ ]:
nn.loss